# Intro

This notebook currently runs at http://saresc-cons-02.psi.ch:8888/lab/tree/RTC%3Aslic/cristallina/acquisition/SF_acquisition03.ipynb. It can be accessed from each Cristallina console using this exact link (password is cristallina). In case something does not work the server can be shutdown via the File menu or CTRL+C in the console window. It can then be restarted using `start_local_jupyter` in the `/sf/cristallina/applications` directory.

Parallel editing now works similar to a Google Docs document thanks to a Jupyter extension (only tested a bit so far).

This might be the start for a template that each experiment receives in the beginning to perform acquisitions.

The stand server accompagnying this experiment is running at http://saresc-vcons-02.psi.ch:8501


In [1]:
from slic.core.adjustable import Adjustable, PVAdjustable, DummyAdjustable
from slic.core.scanner import Scanner
from slic.core.acquisition import BSAcquisition, PVAcquisition, SFAcquisition

from devices.diffractometer import diffractometer

]0;⊚slic

# Setup slic
We run our `cristallina.py` to setup the complete acquisition environment:

In [2]:
%run /sf/cristallina/applications/slic/cristallina/cristallina.py


2023-11-06 at 17:40:43 | INFO | Loading started.


could not set up DBusNotify: org.freedesktop.DBus.Error.AccessDenied: Failed to connect to socket /run/user/43883/bus: Permission denied


2023-11-06 at 17:40:45 | INFO | Connected to stand server
2023-11-06 at 17:40:46 | INFO | Using undulator (Aramis) offset to PSSS energy of -62 eV.
2023-11-06 at 17:40:47 | WARNING | Cannot write log file to pgroup p19150.
2023-11-06 at 17:40:47 | INFO | Running at cristallina with pgroup p19150.
2023-11-06 at 17:40:47 | INFO | Loading finished.


In [5]:
diffractometer

diffractometer:
---------------
td:       129.81409500000018 mm
theta:    0.0004315278828144198°
tr_x:     13.019455000000107 mm
tr_y:     -19.013439999999946 mm
trx_base: 21.773304999999937 mm
try_base: 0.04304476804733426 mm
twotheta: 80.65199162811041°

In [3]:
# setup dummy axis for testing
dummy = DummyAdjustable()
print(f"dummy at: {dummy.get_current_value()}")

dummy at: 0


In [7]:
bs_example_channels = [
    "SARFE10-PBPG050:PHOTON-ENERGY-PER-PULSE-AVG",
    "SARFE10-PBIG050-EVR0:CALCI",
    "SARES30-CAMS156-XE:x_fit_amplitude",
]  # "SARES30-CAMS156-XE:FPICTURE"]

# SFAcquisition example

To acquire data including the Jungfrau detector we have to go through the SF-DAQ pipeline. 
This requires an existing `pgroup`. The `default_data_base_dir` cannot be used to specify arbitrary directories as a target, instead the data is located in `/sf/<instrument>/data/<pgroup>/raw/run<XXXX>/data/acq<YYYY>.*.h5`.

We also setup the `spreadsheet` to be submitted to stand to record all the run information:

In [4]:
# TODO: requires the stand client, need small howto how to start and configure or let it run all the time
from slic.core.acquisition.spreadsheet import Spreadsheet

In [7]:
# setup spreadsheet for transmission to stand
spreadsheet = Spreadsheet(
    {
        "TD": diffractometer.td,
        "TRX": diffractometer.tr_x,
        "TRY": diffractometer.tr_y,
        "TRXBASE": diffractometer.trx_base,
        "TRYBASE": diffractometer.try_base,
        "THETA": diffractometer.theta,
        "TWOTHETA": diffractometer.twotheta,
    },
    placeholders=("comment", "sample"),
    host="saresc-vcons-02.psi.ch",
    port=9090,
)

In [15]:
# spreadsheet.client.add_row(a=2, b=3, c=4)
# spreadsheet.client.clear() # delete stand table completely

In [55]:
# show current diffractometer status
diffractometer

diffractometer:
---------------
td:       103.19394499999999 mm
theta:    11.660351939067244°
tr_x:     0.0 mm
tr_y:     -9.00136499999985 mm
trx_base: 21.89786499999991 mm
try_base: 0.04305062122344694 mm
twotheta: 84.31427503935993°

## Single acquisition example

We setup a single acquisition as part of a run. Again, this requires an existing pgroup.

In [16]:
# setup acquisition
acq = SFAcquisition(
    "cristallina",
    "p19150", # "p21563",
    default_channels=bs_channels,
    default_pvs=pvs,
    spreadsheet=spreadsheet,
    default_detectors=detectors,
    rate_multiplicator=1,
)

And run the acquisition:

In [13]:
acq.acquire("test_acquisition",
    data_base_dir=None,
    n_pulses=100,
    n_repeat=1,
    is_scan_step=False,
    )

Advanced run number to 209.
No detectors specified, using default detector list.
No PVs specified, using default PV list.
No channels specified, using default channel list.
Offline Channels:
-----------------
- SARES30-CAMS156-XE:intensity
- SAROP31-PBPS149:INTENSITY
- SAROP31-PBPS149:INTENSITY_UJ
- SAROP31-PBPS149:XPOS
- SAROP31-PBPS149:YPOS

    run_number                      time                   topic sample                                       comment  ...        TRY    TRXBASE   TRYBASE    THETA   TWOTHETA
0          1.0  Mon Sep 25 21:28:03 2023  Beamline commissioning     --                                                ...        NaN        NaN       NaN      NaN        NaN
1          2.0  Mon Sep 25 22:06:09 2023  Beamline commissioning     --                                                ...        NaN        NaN       NaN      NaN        NaN
2          3.0  Mon Sep 25 22:59:50 2023  Beamline commissioning     --                         Smaract movement test  ...       

100%|████████████████████████████████████████████████████████████████████████████████████████████████████| 100/100 [00:01<00:00,  90.3 Hz]

run number:       209
acq number:       1
total acq number: 706



DAQTask: done

Output files:
-------------
- /sf/cristallina/data/p19150/raw/run0209/data/acq0001.PVDATA.h5
- /sf/cristallina/data/p19150/raw/run0209/data/acq0001.BSDATA.h5
- /sf/cristallina/data/p19150/raw/run0209/data/acq0001.JF16T03V01.h5

## Perform one scan
Similarly we can define a scan which uses acquisition from above to change an adjustable over a certain range, and perform an acquisition at each point:

In [ ]:
scan.scan1D(
    diffractometer.theta,
    11.66-0.3,
    11.66+0.3,
    step_size=0.025,
    n_pulses=60,
    filename="TRXTHETA_405_upper_sample",
    acquisitions=[acq],
    step_info=None,
    return_to_initial_values=False,
)

# BSacquisition

Alternatively we can not use the SF-DAQ infrastructure and only record BS data to any directory. This cannot include Jungfrau data though.

We setup a minimal example as follows:

In [ ]:
bs_example_channels = ['SARFE10-PBPG050:PHOTON-ENERGY-PER-PULSE-AVG', "SARFE10-PBIG050-EVR0:CALCI",  "SARES30-CAMS156-XE:x_fit_amplitude",] # "SARES30-CAMS156-XE:FPICTURE"]

In [ ]:
# setup dummy axis
dummy = DummyAdjustable()
print(f"dummy at: {dummy.get_current_value()}")

# setup scanner
scanner = Scanner(data_base_dir="/tmp/scan_data", scan_info_dir="/tmp/scan_info")

In [ ]:
# setup acquisition 
acq = BSAcquisition('example_instrument', 'example_pgroup', default_channels=bs_example_channels, default_data_base_dir='/tmp')

scanner.scan1D(dummy, 0, 10, step_size=1, n_pulses=10, filename='test_bs', acquisitions=[acq], step_info=None, return_to_initial_values=False)

# Runs in an experiment

With these tests we can now define everything for the actual experiment and perform the measurements.

In [7]:
# setup acquisition

# this requires an existing pgroup
acq = SFAcquisition(
    "cristallina",
    "p21516",
    default_channels=bs_channels,
    default_pvs=pvs,
    spreadsheet=spreadsheet,
    default_detectors=detectors,
    rate_multiplicator=1,
)

scan = Scanner(default_acquisitions=[daq], condition=check_intensity_gas_monitor)


In [8]:
undulators.adjs


{'SARUN03-UIND030': Undulator "SARUN03-UIND030" at 1.7323858702653407 ,
 'SARUN04-UIND030': Undulator "SARUN04-UIND030" at 1.7323858702653407 ,
 'SARUN05-UIND030': Undulator "SARUN05-UIND030" at 1.7323858702653407 ,
 'SARUN06-UIND030': Undulator "SARUN06-UIND030" at 1.7323858702653407 ,
 'SARUN07-UIND030': Undulator "SARUN07-UIND030" at 1.7287122962798656 ,
 'SARUN08-UIND030': Undulator "SARUN08-UIND030" at 1.7331003603559842 ,
 'SARUN09-UIND030': Undulator "SARUN09-UIND030" at 1.7336107470023607 ,
 'SARUN10-UIND030': Undulator "SARUN10-UIND030" at 1.7347154803699962 ,
 'SARUN11-UIND030': Undulator "SARUN11-UIND030" at 1.733388366970084 ,
 'SARUN12-UIND030': Undulator "SARUN12-UIND030" at 1.7324691124462326 ,
 'SARUN13-UIND030': Undulator "SARUN13-UIND030" at 1.7306694932706983 ,
 'SARUN14-UIND030': Undulator "SARUN14-UIND030" at 1.729969640942022 ,
 'SARUN15-UIND030': Undulator "SARUN15-UIND030" at 1.7235709799331544 }

In [ ]:
# careful, this moves the undulators 
scan.scan1D(
    undulators,
    8320,
    8380,
    step_size=2,
    n_pulses=20,
    filename="Undulator_scan",
    acquisitions=[acq],
    step_info=None,
    return_to_initial_values=False,
)

Advanced run number to 54 for SF DAQ on http://sf-daq:10002 (status: idle, last run: 54).
    run                                  filename  n_pulses comment sample                  scanned_adjs    v_min  ...          TD      TRX       TRY    TRXBASE   TRYBASE      THETA   TWOTHETA
0    27                         Rocking_curve_003        50                 SARES30-CPCL-ECMC02:ROTTHETA    11.00  ...  103.193915  0.00000 -7.639270  21.770540  0.043051  12.999782  24.000607
1    28             Rocking_curve_003_slightly_up        50                 SARES30-CPCL-ECMC02:ROTTHETA    11.00  ...  103.193905  0.00000 -7.438835  21.970745  0.043051  12.000128  24.000651
2    29  Rocking_curve_003_slightly_up_few_pulses         5                 SARES30-CPCL-ECMC02:ROTTHETA    11.00  ...  103.193910  0.00000 -7.436310  21.971195  0.043051  13.000497  24.000643
3    30  Rocking_curve_003_slightly_up_few_pulses         1                 SARES30-CPCL-ECMC02:ROTTHETA    11.00  ...  103.193920  0.0000

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████| 20/20 [00:00<00:00,  66.3 Hz]


run number:       54
acq number:       1
total acq number: 2337

DAQTask: done

Output files:
-------------
- /sf/cristallina/data/p21563/raw/run0054/data/acq0001.PVDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0001.BSDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0001.JF16T03V01.h5
Acquisition done
Waited for 13.8 seconds and collected 13 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
Scan step 2 of 31
Waited for 0.5 seconds and collected 1 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
1.739115799580604 <- 8260.0
scaled:    [1.73901368 1.73901368 1.73901368 1.73901368 1.73533728 1.73972872
 1.7402395  1.74134509 1.74001695 1.73909698 1.73729598 1.73659559
 1.73019205]

SARUN03-UIND030: 1.7393634943252434	->	1.7390136759268793	(0.0003498183983641212)
SARUN04-UIND030: 1.7393634943252434	->	1.7390136759268793	(0.0003498183983641212)
SARUN05-UIND030: 1.7393634943252434	->	1.7390136759268793

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████| 20/20 [00:00<00:00,  66.3 Hz]


run number:       54
acq number:       2
total acq number: 2338

DAQTask: done

Output files:
-------------
- /sf/cristallina/data/p21563/raw/run0054/data/acq0002.PVDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0002.BSDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0002.JF16T03V01.h5
Acquisition done
Waited for 9.8 seconds and collected 10 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
Scan step 3 of 31
Waited for 0.5 seconds and collected no(!) data points.
Is the source alive?
Condition is unhappy, waiting for OK conditions since 0.5 seconds.
Waited for 0.5 seconds and collected 1 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
Condition was unhappy, waited for 1.0 seconds.
1.7387322497618714 <- 8262.0
scaled:    [1.73866396 1.73866396 1.73866396 1.73866396 1.73498771 1.73937897
 1.73988973 1.74099527 1.73966719 1.73874726 1.73694633 1.73624597
 1.72984269]

SARUN03-UIND030: 1.73901367592

...

run number:       54
acq number:       5
total acq number: 2341

DAQTask: done

Output files:
-------------
- /sf/cristallina/data/p21563/raw/run0054/data/acq0005.PVDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0005.BSDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0005.JF16T03V01.h5
Acquisition done
Waited for 9.6 seconds and collected 9 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
Scan step 6 of 31
Waited for 0.5 seconds and collected 1 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
1.7376144533739812 <- 8268.0
scaled:    [1.73761539 1.73761539 1.73761539 1.73761539 1.73393959 1.73833032
 1.73884101 1.73994642 1.7386185  1.73769868 1.73589797 1.7351977
 1.7287952 ]

SARUN03-UIND030: 1.7379648146610862	->	1.7376153920049042	(0.00034942265618198576)
SARUN04-UIND030: 1.7379648146610862	->	1.7376153920049042	(0.00034942265618198576)
SARUN05-UIND030: 1.7379648146610862	->	1.7376153920049042

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████| 20/20 [00:00<00:00,  66.3 Hz]


run number:       54
acq number:       6
total acq number: 2342

DAQTask: done

Output files:
-------------
- /sf/cristallina/data/p21563/raw/run0054/data/acq0006.PVDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0006.BSDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0006.JF16T03V01.h5
Acquisition done
Waited for 9.7 seconds and collected 10 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
Scan step 7 of 31
Waited for 0.5 seconds and collected no(!) data points.
Is the source alive?
Condition is unhappy, waiting for OK conditions since 0.5 seconds.
Waited for 0.5 seconds and collected 1 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
Condition was unhappy, waited for 1.0 seconds.
1.7372651295337658 <- 8270.0
scaled:    [1.73726607 1.73726607 1.73726607 1.73726607 1.73359042 1.73798096
 1.73849164 1.739597   1.73826913 1.73734936 1.73554872 1.73484847
 1.72844623]

SARUN03-UIND030: 1.73761539200

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████| 20/20 [00:00<00:00,  66.3 Hz]


run number:       54
acq number:       7
total acq number: 2343

DAQTask: done

Output files:
-------------
- /sf/cristallina/data/p21563/raw/run0054/data/acq0007.PVDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0007.BSDATA.h5
- /sf/cristallina/data/p21563/raw/run0054/data/acq0007.JF16T03V01.h5
Acquisition done
Waited for 9.8 seconds and collected 9 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
Scan step 8 of 31
Waited for 0.5 seconds and collected 1 data points.
Condition happy: 100.0% within limits [-100, 2000), required was 80.0%.
1.736971368932527 <- 8272.0
scaled:    [1.73691684 1.73691684 1.73691684 1.73691684 1.73324134 1.73763171
 1.73814237 1.73924768 1.73791987 1.73700013 1.73519956 1.73449935
 1.72809736]

SARUN03-UIND030: 1.7372660681263836	->	1.7369168429624722	(0.00034922516391144853)
SARUN04-UIND030: 1.7372660681263836	->	1.7369168429624722	(0.00034922516391144853)
SARUN05-UIND030: 1.7372660681263836	->	1.7369168429624722